In [221]:
import datatoolbox as dt
import pandas as pd
import numpy as np


In [329]:
# Read in targets data
targets = pd.read_excel("tool/Data prep/unsg/country_targets_and_refyears.xlsx", header = 3)

In [224]:
# All GHGs including LULUCF (historical data)
ghgs = dt.getTable(dt.findp(source = "UNFCCC_CRF_2020", variable = "Emissions|KYOTOGHG_AR4|IPC0").index[0])

In [434]:
ghgs_nolu = dt.getTable(dt.findp(source = "UNFCCC_CRF_2020", variable = "Emissions|KYOTOGHG_AR4|IPCM0EL").index[0])

In [225]:
lulucf = dt.getTable(dt.findp(source = "UNFCCC_CRF_2020", variable = "Emissions|KYOTOGHG_AR4|LULUCF").index[0])

In [330]:
g7_list = ['CAN','DEU','FRA','GBR','ITA','JPN','USA']
g7 = targets.loc[targets['country'].isin(g7_list)].set_index('country')

In [331]:
# Find ref values
for cntry in g7_list:
    year = g7.loc[cntry, 'Reference_year']
    g7.loc[cntry,'Ref_value'] = ghgs.loc[cntry, year]
    g7.loc[cntry,'value_1990'] = ghgs.loc[cntry, 1990]
    g7.loc[cntry,'value_2010'] = ghgs.loc[cntry, 2010]
    g7.loc[cntry,'lulucf_2010'] = lulucf.loc[cntry, 2010]

In [332]:
# calculate targets including lulucf
# new targets
g7['target_min'] = g7['Ref_value']*(1 - g7['New_target'])
g7['target_max'] = g7['Ref_value']*(1 - g7['New_target_max'])

# old targets
# calculate targets

g7['oldtarget_min'] = g7['Ref_value']*(1 - g7['Old _target'])
g7['oldtarget_max'] = g7['Ref_value']*(1 - g7['Old_target_max'])
g7.loc['USA','oldtarget_min'] = g7.loc['USA', 'Old_target_abs']
g7.loc['USA','oldtarget_max'] = g7.loc['USA', 'Old_target_abs_max']

In [333]:
g7

type  Reference_year  Old _target  Old_target_max  Old_target_abs  \
country                                                                     
USA       G7            2005         0.26            0.28        4051.432   
JPN       G7            2013         0.26            0.26             NaN   
CAN       G7            2005         0.30            0.30             NaN   
GBR       G7            1990         0.57            0.57             NaN   
ITA       G7            1990         0.30            0.30             NaN   
FRA       G7            1990         0.40            0.40             NaN   
DEU       G7            1990         0.55            0.55             NaN   

         Old_target_abs_max  New_target  New_target_max CAT_abs_NDC  \
country                                                               
USA                4156.664        0.50            0.52         NaN   
JPN                     NaN        0.46            0.46         NaN   
CAN                     NaN        0.40            0.45         NaN   
GBR                     NaN        0.68            0.68         NaN   
ITA                     NaN        0.60            0.60         NaN   
FRA                     NaN        0.40            0.40         NaN   
DEU                     NaN        0.65            0.65         NaN   

         CAT_abs_NDCmax                                              Notes  \
country                                                                      
USA                 NaN  Calculated in NDC update calculations assuming...   
JPN                 NaN                                                NaN   
CAN                 NaN                                                NaN   
GBR                 NaN                                                NaN   
ITA                 NaN  To check; assumes same level for Italy as for ...   
FRA                 NaN                                           To check   
DEU                 NaN                                                NaN   

           Ref_value   value_1990   value_2010  lulucf_2010   target_min  \
country                                                                    
USA      6577.089624  5583.629723  6241.086066  -740.526979  3288.544812   
JPN      1341.785871  1207.821339  1232.102365   -70.447604   724.564370   
CAN       717.041011   543.595163   665.287095   -25.243522   430.224607   
GBR       797.944507   797.944507   605.642283    -8.850936   255.342242   
ITA       512.495818   512.495818   471.781754   -41.974625   204.998327   
FRA       529.805825   529.805825   480.111136   -36.882451   317.883495   
DEU      1220.646039  1220.646039   922.674521   -19.663477   427.226113   

          target_max  oldtarget_min  oldtarget_max  
country                                             
USA      3157.003020    4051.432000    4156.664000  
JPN       724.564370     992.921544     992.921544  
CAN       394.372556     501.928708     501.928708  
GBR       255.342242     343.116138     343.116138  
ITA       204.998327     358.747073     358.747073  
FRA       317.883495     317.883495     317.883495  
DEU       427.226113     549.290717     549.290717

In [230]:
reduction1990_min = (1-g7['target_min'].sum()/g7['value_1990'].sum())*100
reduction1990_max = (1-g7['target_max'].sum()/g7['value_1990'].sum())*100
reduction2010_min = (1-g7['target_min'].sum()/g7['value_2010'].sum())*100
reduction2010_max = (1-g7['target_max'].sum()/g7['value_2010'].sum())*100

In [231]:
# G7 reduction from 2010 levels (incl LULUCF):
print(reduction2010_min, reduction2010_max)

46.80335795427987 48.37976632841846


In [338]:
# G7 reduction from old targets
del_ambition_mins = (1-g7['target_min'].sum()/g7['oldtarget_min'].sum())*100
del_ambition_maxs = (1-g7['target_max'].sum()/g7['oldtarget_max'].sum())*100
print(del_ambition_mins, del_ambition_maxs)

20.610960225148624 24.08626971222496


In [459]:
# Find EU27 target (incl LULUCF)
EU27_list = ['AUT', 'BEL', 'BUL','HRV','CYP','CZE','DNK','EST','FIN','FRA','DEU','GRC','HUN','IRL','ITA','LVA','LTU','LUX',
            'MLT','NLD','POL','PTG','ROU','SVK','SVN','ESP','SWE']
eu27_ref = ghgs.loc[ghgs.index.isin(EU27_list), 1990].sum()
eu27_2010 = ghgs.loc[ghgs.index.isin(EU27_list), 2010].sum()
eu27_2010_nolu = ghgs_nolu.loc[ghgs_nolu.index.isin(EU27_list), 2010].sum()

eu27_target = (1-0.55)*eu27_ref

In [457]:
g7_eu_min = g7.loc[['USA','JPN','CAN','GBR'],'target_min'].sum() + eu27_target
g7_eu_max = g7.loc[['USA','JPN','CAN','GBR'],'target_max'].sum() + eu27_target
g7_eu_2010 = g7.loc[['USA','JPN','CAN','GBR'],'value_2010'].sum() + eu27_2010

In [458]:
# G7 + EU27 reduction from 2010 levels (incl LULUCF):

print(1 - g7_eu_max/g7_eu_2010, 1 - g7_eu_min/g7_eu_2010)

0.4771406756842296 0.4637554725123867


In [349]:
# G7 + EU27 reduction from previous NDC (incl LULUCF):
# old EU28 target was 40% below 1990, incl LULUCF
EU28_list = ['AUT', 'BEL', 'BUL','HRV','CYP','CZE','DNK','EST','FIN','FRA','DEU','GRC','HUN','IRL','ITA','LVA','LTU','LUX',
            'MLT','NLD','POL','PTG','ROU','SVK','SVN','ESP','SWE','GBR']
eu28_ref = ghgs.loc[ghgs.index.isin(EU28_list), 1990].sum()
eu28_target = (1-0.4)*eu28_ref

g7_eu_old = g7.loc[['USA','JPN','CAN'], 'oldtarget_min'].sum() + eu28_target
g7_eu_old_max = g7.loc[['USA','JPN','CAN'], 'oldtarget_max'].sum() + eu28_target

print(1 - g7_eu_min / g7_eu_old, 1 - g7_eu_max / g7_eu_old_max)

0.22932726316248708 0.2575426984929372


In [454]:
EU28_list = ['AUT', 'BEL', 'BUL','HRV','CYP','CZE','DNK','EST','FIN','FRA','DEU','GRC','HUN','IRL','ITA','LVA','LTU','LUX',
            'MLT','NLD','POL','PTG','ROU','SVK','SVN','ESP','SWE','GBR']
eu28_2018 = ghgs_nolu.loc[ghgs_nolu.index.isin(EU28_list), 2018].sum()
print(eu28_2018)
ghgs_nolu.loc['EU28',2018]

4111.86984617924


4225.027980955379

In [351]:
# G7 NDC emissions and emissions reductions from 2010 *excluding* land-use change

ndc_nolu = pd.read_excel('UK_COP_analysis/NDC update calculations Jun2021.xlsx', sheet_name='for_analysis', header = 1).set_index('country')
non_eu_g7 = ['USA','CAN','JPN','GBR']
ndc_noneu = ndc_nolu.loc[non_eu_g7, 'NDC'].values.sum()
ndc_noneu_max = ndc_nolu.loc[non_eu_g7, 'NDC_max'].values.sum()

# assume EU countries exclude LULUCF (i.e. LULUCF should be zero) to find total target level excl lulucf
g7ndc_nolu_min = ndc_noneu + g7.loc[['FRA', 'ITA','DEU'],'target_min'].values.sum()
g7ndc_nolu_max = ndc_noneu_max + g7.loc[['FRA', 'ITA','DEU'],'target_max'].values.sum()

# find historical lulucf for G7:
g7_lu_hist = g7.loc[g7_list, 'lulucf_2010'].values.sum()
g7_hist_nolu = g7.loc[g7_list, 'value_2010'].values.sum() - g7_lu_hist

# G7 reduction from 2010 (excl LULUCF)

print(1 - g7ndc_nolu_min / g7_hist_nolu, 1 - g7ndc_nolu_max / g7_hist_nolu) 


0.46886680736758257 0.42207670691258936


In [363]:
# Find change from previous target - G7 + EU (*excluding* LULUCF)
# Old G7+EU targets excl LULUCF
g7eu_old_nolu = ndc_nolu.loc[['EU28','CAN','JPN','USA'], 'NDC_old'].sum()
g7eu_old_nolu_max = ndc_nolu.loc[['EU28','CAN','JPN','USA'], 'NDC_old_max'].sum()

#find g7+EU targets excl LULUCF
g7eu_nolu = ndc_nolu.loc[['EU27','GBR','CAN','JPN','USA'], 'NDC'].sum()
g7eu_nolu_max = ndc_nolu.loc[['EU27','GBR','CAN','JPN','USA'], 'NDC_max'].sum()

print(1 - g7eu_nolu / g7eu_old_nolu, 1 - g7eu_nolu_max / g7eu_old_nolu_max)


0.22891647781994173 0.2004296116196692


In [480]:
# G7 + EU reductions from 2010 excluding land-use change
# g7eu_hist_nolu = g7_eu_2010
eu27_2010_nolu = ghgs_nolu.loc[ghgs_nolu.index.isin(EU27_list), 2010].sum()
g7eu_2010_nolu = ghgs_nolu.loc[['CAN','JPN','USA','GBR'], 2010].sum() + eu27_2010_nolu
print(g7eu_2010_nolu)

# G7 + EU reduction from 2010 *excluding* LULUCF
print(1 - g7eu_nolu / g7eu_2010_nolu, 1 - g7eu_nolu_max / g7eu_2010_nolu)

13652.265863327519
0.45906415287168856 0.4095485628028004


In [483]:
print(g7eu_2010_nolu, g7_eu_2010)

13652.265863327519 12505.887351578504


In [370]:
# Change from previous target - G7 excluding LULUCF
# Old G7 targets excl LULUCF: assume EU countries' targets include zero LULUCF)
frdeit = g7.loc[['FRA','DEU','ITA'], 'oldtarget_min'].sum()
frdeit_max = g7.loc[['FRA','DEU','ITA'], 'oldtarget_max'].sum()
g7_old_nolu = ndc_nolu.loc[['GBR','CAN','JPN','USA'], 'NDC_old'].sum() + frdeit
g7_old_nolu_max = ndc_nolu.loc[['GBR','CAN','JPN','USA'], 'NDC_old_max'].sum() + frdeit_max

print(1 - g7ndc_nolu_min / g7_old_nolu_max, 1 - g7ndc_nolu_max / g7_old_nolu_max)

0.2551344035626686 0.18951557844267353


## Domestic pathways and equity

In [371]:
## Find gap in domestic pathways and equity

dp_data = pd.read_excel('UK_COP_analysis/20210420-domesticpathways-quantiles.xlsx')
equity_data = pd.read_excel('UK_COP_analysis/210309_range_p5_proc_CAT_EU27.xlsx')

In [372]:
countries = ['EU28','GBR','CAN','JPN','USA','FRA','DEU','ITA']
countries_tosum = ['EU28','CAN','JPN','USA']
dp15_data = dp_data.loc[(dp_data['sr15_kind'] == 'Below 1.5C and low overshoot')
                       & (dp_data['quantile'] == 0.5)
                       & (dp_data['region'].isin(countries_tosum)),
                       2030]
dp_2030_g7eu = dp15_data.values.sum()*1000

In [486]:
# Reduction from 2010 for G7+EU required for 1.5 compatability (excl LULUCF)
print(1 - (dp_2030_g7eu / g7eu_2010_nolu)) 

# Reduction from current G7+EU targets required for 1.5 compatability (excl LULUCF)
print(1 - (dp_2030_g7eu / g7eu_nolu), 1 - (dp_2030_g7eu / g7eu_nolu_max))

# Reduction from old G7+EU targets required for 1.5 compatability (excl LULUCF)
print(1 - (dp_2030_g7eu / g7eu_old_nolu), 1 - (dp_2030_g7eu / g7eu_old_nolu_max) )

0.5383611499395655
0.14659223915154496 0.21815949462029027
0.34195133790917653 0.3748634834620713


In [389]:
#CHECK to see if reduction makes sense
print((1-0.3419)*g7eu_old_nolu, dp_2030_g7eu)

6302.907999200001 6302.4163138658405


In [377]:
# Find total fair share level for G7+EU
countries_tosum_eq = ['EU27','GBR','CAN','JPN','USA']
eq15_data = equity_data.loc[(equity_data['scenario'] == '2100_GMT<1.5C@P0.5')
                       & (equity_data['region'].isin(countries_tosum_eq)),
                       '2030_allowances']
eq_2030_g7eu = eq15_data.values.sum()
eq_2030_g7eu

2806.3778011784625

In [488]:
### ADD G7 EU hist values excluding LULUCF

# Reduction from 2010 for G7+EU required for fair share 1.5 (excl LULUCF)
print(1 - (eq_2030_g7eu / g7eu_2010_nolu))

# Reduction from current NDCs required for fair share (excl LULUCF)
print(1 - eq_2030_g7eu / g7eu_nolu, 1 - eq_2030_g7eu / g7eu_nolu_max)

# Reduction from old NDCs required for fair share (excl LULUCF)
print(1 - eq_2030_g7eu / g7eu_old_nolu, 1 - eq_2030_g7eu / g7eu_old_nolu_max)

0.7944386793171889
0.6199894649724492 0.6518573624639049
0.7069801381854277 0.7216354560935117


In [487]:
# Gap to 1.5 domestic pathway as share of emissions under current NDC target (i.e. how much lower)
print((g7eu_nolu - dp_2030_g7eu)/g7eu_nolu)
print((g7eu_nolu_max - dp_2030_g7eu)/g7eu_nolu_max)


0.14659223915154496
0.21815949462029022


In [210]:
eq_2030_g7eu

2806.3778011784625

In [438]:
# Estimate portion of current emissions covered by G7 (excludes LULUCF)
g7_2018 = ghgs_nolu.loc[g7_list, 2018].sum()
cat_hist = pd.read_excel('tool/Data prep/Data/CATFINAL_201124_data.xlsx', header = 28, sheet_name= 'CATFINAL_PLEDGEHI_CATM0EL')
cat_ext = pd.read_excel('tool/Data prep/Data/CATEXT_201124_data.xlsx', header = 28, sheet_name= 'CATEXT_PLEDGEHI_CATM0EL').set_index('Countries\Years')
cat_hist.loc[0,'2018']
print(g7_2018/cat_hist.loc[0,'2018'])

0.22798846029864606


In [439]:
ghgs_nolu.loc['EU28', 2018]

4225.027980955379

In [496]:
ghgs_nolu.loc[g7_list, 2018].sum()/48550

0.223447597464249

In [505]:
cat_ext_policy_hi = pd.read_excel('tool/Data prep/Data/CATEXT_201124_data.xlsx', header = 28, sheet_name= 'CATEXT_TRENDHI_CATM0EL').set_index('Countries\Years')
cat_ext_policy_lo = pd.read_excel('tool/Data prep/Data/CATEXT_201124_data.xlsx', header = 28, sheet_name= 'CATEXT_TRENDLO_CATM0EL').set_index('Countries\Years')


In [507]:
g7eu_policy_hi = cat_ext_policy_hi.loc[['USA','EU28','CAN','JPN'], 2030].sum()
g7eu_policy_lo = cat_ext_policy_lo.loc[['USA','EU28','CAN','JPN'], 2030].sum()

In [508]:
# calculate reduction from 2010 levels for current policies in 2030 (excl lulucf)
print(1 - g7eu_policy_hi / g7eu_2010_nolu, 1 - g7eu_policy_lo / g7eu_2010_nolu)

0.12791767174843682 0.2109435233797593


In [510]:
g7eu_policy_hi

11905.8998